# LOAD DATA

**Objective**: In here the data is readed and adapted to the same format, to ease when needed to be joined.

Loaded data in the following order:
1. [Main.paquet](#1.-Main-dataset): this is the main data provided. In here we will find the most relevant features + the output variable. As is explained on the [README.md](https://github.com/saraalgo/LSTM-for-regression/blob/main/README.md), this  is proprietary data.
2. [Climate](#2.-Climate): these are climate variables that comes from the public repository [NOAA](https://www.ncei.noaa.gov/cdo-web/webservices/v2). Despite being a public repository, this data has been preprocessed by a third party, so can not be shared in this point.
2. [Cropland in US](#3.-Cropland-use-for-cops-on-each-state-US): public data that can be found on [USDA-NASS](https://www.nass.usda.gov/Data_and_Statistics/).

## Load packages

In [3]:
# Set Git path
import os 
CURRENT_PATH = os.getcwd()

# Data manipulation
from pathlib import Path
import pandas as pd
import csv
from ydata_profiling import ProfileReport

In [4]:
outpath = Path('../../data/01-Preprocessing/')
outpath.mkdir(exist_ok=True, parents=True)

## 1. Main data

In [5]:
corn_raw = pd.read_parquet('../../data/00-Raw/Main/main.parquet')
#corn_raw.head()

#### Check filters desired and get the main only with the output feature:

1. `FILTER the dataset for STATISTICCAT == Area Planted, Acres Harvested, Yield`

2. `Filter for AGG_LEVEL_DESC == STATE`

3. `SHORT_DESC == CORN - ACRES PLANTED`

4. `REFERENCE_PERIOD_DESC == YEAR`

All filters applied

In [6]:
# Apply filters
filter1 = corn_raw[corn_raw['STATISTICCAT_DESC'].isin(['AREA PLANTED','AREA HARVESTED','YIELD'])]
filter2 = filter1[filter1['AGG_LEVEL_DESC'] == 'STATE']
filter3 = filter2[filter2['SHORT_DESC'] == 'CORN - ACRES PLANTED']
filter4 = filter3[filter3['REFERENCE_PERIOD_DESC'] == 'YEAR']
#filter4.head()

To check if any of the other columns apart from: **'VALUE'**,**'STATISTICCAT_DESC'**, **'LOCATION_DESC'** and **'YEAR'** are relevant

In [7]:
profile_filter4 = ProfileReport(filter4)
profile_filter4

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [8]:
# Get main DF from filters
maindf = filter4[['VALUE','STATISTICCAT_DESC', 'LOCATION_DESC', 'YEAR']].copy()

profile_maindf = ProfileReport(maindf)
profile_maindf

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

After checking the profiling, there are needed changes in the **VALUE** and **LOCATION_DESC** columns

In [9]:
# Give correct format to value column
maindf['VALUE'] = maindf['VALUE'].str.replace(r',[^,]*$', '', regex=True)
maindf['VALUE'] = maindf['VALUE'].str.replace(',', '').astype(float)

# Only rows with LOCATION_DESC defined
maindf = maindf[maindf['LOCATION_DESC'] != 'OTHER STATES']

In [10]:
# Pivot to use each STATISTICCAT_DESC as feature
main_output = maindf.pivot(index=['YEAR','LOCATION_DESC'], columns=['STATISTICCAT_DESC'], values='VALUE')
main_output.reset_index(inplace=True)

In [11]:
main_output

STATISTICCAT_DESC  YEAR  LOCATION_DESC  AREA PLANTED
0                  1919        ARIZONA          31.0
1                  1920        ARIZONA          29.0
2                  1921        ARIZONA          35.0
3                  1922        ARIZONA          39.0
4                  1923        ARIZONA          33.0
...                 ...            ...           ...
4642               2022       VIRGINIA         480.0
4643               2022     WASHINGTON         140.0
4644               2022  WEST VIRGINIA          46.0
4645               2022      WISCONSIN        3950.0
4646               2022        WYOMING          95.0

[4647 rows x 3 columns]

#### Main with more features besides filters

Applied:
- FILTER 2: **AGG_LEVEL_DESC** == *STATE*
- FILTER 4: **REFERENCE_PERIOD_DESC** == *YEAR*
- And take all combinations of **STATISTICCAT_DESC** and **SHORT_DESC** features

In [12]:
filter2 = corn_raw[corn_raw['AGG_LEVEL_DESC'] == 'STATE']
filter4 = filter2[filter2['REFERENCE_PERIOD_DESC'] == 'YEAR']
main = filter4.copy()

# remain with the same subset that main
main = main[['VALUE','STATISTICCAT_DESC', 'SHORT_DESC', 'LOCATION_DESC', 'YEAR']].copy()

In [13]:
# Give correct format to value column
main['VALUE'] = main['VALUE'].str.replace(r',[^,]*$', '', regex=True)
main['VALUE'] = main['VALUE'].str.replace(',', '')
main['VALUE'] = pd.to_numeric(main['VALUE'], errors='coerce')

# Only rows with LOCATION_DESC defined
main = main[main['LOCATION_DESC'] != 'OTHER STATES']

In [14]:
# Pivot to use each SHORT_DESC as feature
main_pivot = main.pivot_table(index=['YEAR','LOCATION_DESC'], columns=['SHORT_DESC'], values='VALUE')

# Filter by y data -> CORN - ACRES PLANTED
main_pivot.dropna(subset=['CORN - ACRES PLANTED'], inplace=True)

main_pivot.reset_index(inplace=True)
main_pivot = main_pivot.rename_axis(None, axis=1)

main_pivot

YEAR  LOCATION_DESC  CORN - ACRES PLANTED  CORN - OPERATIONS WITH SALES  \
0     1919        ARIZONA                  31.0                           NaN   
1     1920        ARIZONA                  29.0                           NaN   
2     1921        ARIZONA                  35.0                           NaN   
3     1922        ARIZONA                  39.0                           NaN   
4     1923        ARIZONA                  33.0                           NaN   
...    ...            ...                   ...                           ...   
4642  2022       VIRGINIA                 480.0                           NaN   
4643  2022     WASHINGTON                 140.0                           NaN   
4644  2022  WEST VIRGINIA                  46.0                           NaN   
4645  2022      WISCONSIN                3950.0                           NaN   
4646  2022        WYOMING                  95.0                           NaN   

      CORN - SALES, MEASURED IN $  \
0                             NaN   
1                             NaN   
2                             NaN   
3                             NaN   
4                             NaN   
...                           ...   
4642                          NaN   
4643                          NaN   
4644                          NaN   
4645                          NaN   
4646                          NaN   

      CORN - SALES, MEASURED IN PCT OF FARM OPERATIONS  \
0                                                  NaN   
1                                                  NaN   
2                                                  NaN   
3                                                  NaN   
4                                                  NaN   
...                                                ...   
4642                                               NaN   
4643                                               NaN   
4644                                               NaN   
4645                                               NaN   
4646                                               NaN   

      CORN - SALES, MEASURED IN PCT OF FARM SALES  \
0                                             NaN   
1                                             NaN   
2                                             NaN   
3                                             NaN   
4                                             NaN   
...                                           ...   
4642                                          NaN   
4643                                          NaN   
4644                                          NaN   
4645                                          NaN   
4646                                          NaN   

      CORN, BIOTECH - AREA PLANTED, MEASURED IN PCT BY TYPE  \
0                                                   NaN       
1                                                   NaN       
2                                                   NaN       
3                                                   NaN       
4                                                   NaN       
...                                                 ...       
4642                                                NaN       
4643                                                NaN       
4644                                                NaN       
4645                                               91.0       
4646                                                NaN       

      CORN, BIOTECH, BT - AREA PLANTED, MEASURED IN PCT BY TYPE  \
0                                                   NaN           
1                                                   NaN           
2                                                   NaN           
3                                                   NaN           
4                                                   NaN           
...                                                 ...           
4642                        

#### Save main datasets

In [15]:
main_output.to_pickle(outpath/'main_output.pkl')
main_pivot.to_pickle(outpath/'main.pkl')

## 2 Climate

In [16]:
# Create dictionary with all subfolders and pathfiles

pathfiles_dict = {}
files_dict = {}

for folder_path, folders, files in os.walk('../../data/00-Raw/Climate/'):
    # Create a list to store filenames for the current subfolder
    subfolder_filenames = []
    for file in files:
        # Append the filename to the list
        subfolder_filenames.append(os.path.join(folder_path, file))
    # Store the list of filenames in the dictionary with the subfolder path as the key
    pathfiles_dict[folder_path] = subfolder_filenames

pathfiles_dict.pop('../../data/00-Raw/Climate/')

prefix_to_remove = '../../data/00-Raw/Climate/'
for key in pathfiles_dict:
    updated_key = key.replace(prefix_to_remove, '', 1)
    files_dict[updated_key] = pathfiles_dict[key]

In [17]:
# Get dataframe of all metrics and pivot it

metric = pd.DataFrame()

def get_start_row(file):
    with open(file, 'r') as file:
        reader = csv.reader(file)
        for i, row in enumerate(reader):
            # Check if the row matches the condition
            if row[0] == 'Date':
                start_row = i
                break
    return start_row

for key in files_dict.keys():
    for file in files_dict[key]:
        if file.endswith('.csv'):  # Check if the file is a CSV file
            # Read state and metric info
            df = pd.read_csv(file, nrows=1, header=None)
            # Find in which row starts the values
            start_row = get_start_row(file)
            # Append the data to the main dataframe
            temp_df = pd.read_csv(file, skiprows = start_row, header=0)
            temp_df = temp_df.assign(State = df[0][0], Metric = df[1][0])
            metric = pd.concat([metric, temp_df], ignore_index=True)
            
# remove anomaly column and rename Date
metric = metric.drop('Anomaly', axis=1)
rename_cols = {'Date': 'DATE'}
metric.rename(columns=rename_cols, inplace=True)

# pivot to get climate df
climate = metric.pivot(index=['DATE','State'], columns='Metric', values='Value')
climate.reset_index(inplace=True)

In [18]:
# Format date format equally than in main df  - here only year and month
climate['DATE'] = pd.to_datetime(climate['DATE'], format='%Y%m')
climate['DATE'] = climate['DATE'].dt.strftime('%Y-%m')

# Ver correlación de media/mediana/sd con estado por año
climate = climate.rename_axis(None, axis=1)
climate

DATE          State   Average Temperature   Cooling Degree Days  \
0      1895-01        Alabama                  43.1                   5.0   
1      1895-01        Arizona                  40.4                   0.0   
2      1895-01       Arkansas                  36.1                   0.0   
3      1895-01     California                  40.5                   0.0   
4      1895-01       Colorado                  21.6                   0.0   
...        ...            ...                   ...                   ...   
74360  2022-01       Virginia                  32.9                   0.0   
74361  2022-01     Washington                  31.2                   0.0   
74362  2022-01  West Virginia                  27.4                   0.0   
74363  2022-01      Wisconsin                   9.2                   0.0   
74364  2022-01        Wyoming                  23.0                   0.0   

        Heating Degree Days   Maximum Temperature   Minimum Temperature  \
0                     716.0                  52.7                  33.4   
1                     508.0                  49.0                  31.8   
2                     914.0                  46.0                  26.2   
3                     654.0                  47.4                  33.6   
4                    1355.0                  33.6                   9.6   
...                     ...                   ...                   ...   
74360                 994.0                  42.8                  23.1   
74361                 869.0                  37.0                  25.4   
74362                1155.0                  37.0                  17.8   
74363                1622.0                  19.6                  -1.3   
74364                1270.0                  34.7                  11.2   

        Palmer Drought Severity Index (PDSI)   Precipitation  
0                                       0.78            7.52  
1                                       1.67            2.78  
2                                       0.37            5.04  
3                                       2.23            9.25  
4                                       1.64            1.96  
...                                      ...             ...  
74360                                  -1.34            4.51  
74361                                   1.44            6.58  
74362                                   0.72            4.86  
74363                                  -1.46            0.50  
74364                                  -4.31            0.79  

[74365 rows x 9 columns]

In [19]:
climate.to_pickle(outpath/'climate.pkl')

## 3. Cropland in US by state

In [23]:
# Read exdata
cropland_state = pd.read_excel('../../data/00-Raw/Cropland_us_state/Cropland_us_state.xls', index_col=None, skiprows=2)
cropland_state = cropland_state.iloc[4:72]

# Filter empty rows
cropland_state = cropland_state.dropna()

# Fill years
cropland_state.set_index('Regions and States', inplace=True)

# Create columns for all intermediate years
cropland_state.columns = cropland_state.columns.astype(str)
years = [int(col) for col in cropland_state.columns]
for idx, year in enumerate(range(min(years), max(years)+4)):
    if str(year) in cropland_state.columns:
        last = cropland_state.iloc[:, idx]
    if str(year) not in cropland_state.columns:
        cropland_state.insert(idx, year, last)

cropland_state = cropland_state.reset_index()

# Melt df
df_dropped = cropland_state.drop('Regions and States', axis=1)
cropland_state_melted = pd.melt(cropland_state, id_vars='Regions and States', value_vars=df_dropped,
                                                var_name='YEAR', value_name='VALUE')

cropland_state = cropland_state_melted.copy()
cropland_state.to_pickle(outpath/'cropland_state.pkl')
cropland_state

Regions and States  YEAR         VALUE
0             Northeast  1945         20904
1                Maine   1945          1331
2         New Hampshire  1945           443
3               Vermont  1945          1171
4         Massachusetts  1945           589
...                 ...   ...           ...
4184             Nevada  2015       478.006
4185            Pacific  2015  17395.510277
4186         Washington  2015      5557.553
4187             Oregon  2015   3522.318277
4188         California  2015      8315.639

[4189 rows x 3 columns]